# Do-It-Yourself

In this session, we will practice your skills in mapping with Python. Fire up a notebook you can edit interactively, and let's do this!



In [1]:
import geopandas, osmnx

In [2]:
osmnx.config(
    overpass_settings='[out:json][timeout:90][date:"2020-09-07T00:00:00Z"]'
)

## Data preparation

### Polygons

For this section, you will have to push yourself out of the comfort zone when it comes to sourcing the data. As nice as it is to be able to pull a dataset directly from the web at the stroke of a url address, most real-world cases are not that straight forward. Instead, you usually have to download a dataset manually and store it locally on your computer before you can get to work.

We are going to use data from the Consumer Data Research Centre (CDRC) about Liverpool, in particular an extract from the Census. You can download a copy of the data at:

```{admonition} Important
You will need a username and password to download the data. Create it for free at:

> [https://data.cdrc.ac.uk/user/register](https://data.cdrc.ac.uk/user/register)
```

> [Liverpool Census'11 Residential data pack download](https://data.cdrc.ac.uk/system/files/Census_Residential_Data_Pack_2011/Census_Residential_Data_Pack_2011_E08000012.zip)

Once you have the `.zip` file on your computer, right-click and "Extract all". The resulting folder will contain all you need. For the sake of the example, let's assume you place the resulting folder in the same location as the notebook you are using. If that is the case, you can load up a `GeoDataFrame` of Liverpool neighborhoods with:

```python
import geopandas
liv = geopandas.read_file("Census_Residential_Data_Pack_2011_E08000012/data/Census_Residential_Data_Pack_2011/Local_Authority_Districts/E08000012/shapefiles/E08000012.shp")
```

### Lines

For a line layer, we are going to use a different bit of `osmnx` functionality that will allow us to extract all the highways:

In [3]:
bikepaths = osmnx.graph_from_place("Liverpool, UK", network_type="bike")

---

Note the code cell above requires internet connectivity. If you are not online but have a full copy of the GDS course in your computer (downloaded as suggested in the [infrastructure page](../infrastructure)), you can read the data with the following line of code: 

In [4]:
bikepaths = osmnx.load_graphml("../data/web_cache/bikepaths_liverpool.graphml")

---

In [5]:
len(bikepaths)

23481

### Points

For points, we will use an analogue of the POI layer we have used in the [Lab](lab_C): pubs in Liverpool, as recorded by OpenStreetMap. We can make a similar query to retrieve the table:

In [6]:
pubs = osmnx.geometries_from_place(
    "Liverpool, UK", tags={"amenity": "bar"}
)

````{attention}
:class: dropdown

If you are using an old version of `osmnx` (<1.0), replace the code in the cell above for:

```python
pubs = osmnx.pois.pois_from_place(
    "Liverpool, UK", tags={"amenity": "bar"}
)
```

You can check the version you are using with the following snipet:

```python
osmnx.__version__
```
````

---

Note the code cell above requires internet connectivity. If you are not online but have a full copy of the GDS course in your computer (downloaded as suggested in the [infrastructure page](../infrastructure)), you can read the data with the following line of code: 

In [7]:
pubs = geopandas.read_parquet("../data/web_cache/pois_bars_liverpool.parquet")

/opt/conda/lib/python3.8/site-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


---

## Tasks

### Task I: *Tweak your map*

With those three layers, try to complete the following tasks:

- Make a map of the Liverpool neighborhoods that includes the following characteristics:

    - Features a title
    - Does not include axes frame
    - It has a figure size of 10 by 11
    - Polygons are all in color `"#525252"` and 50% transparent
    - Boundary lines ("edges") have a width of 0.3 and are of color `"#B9EBE3"`
    - Includes a basemap with the [Stamen watercolor theme](https://contextily.readthedocs.io/en/latest/providers_deepdive.html#Overview-of-built-in-providers)
    
```{Note}
Not all of the requirements above are not equally hard to achieve. If you can get some but not all of them, that's also great! The point is you learn something every time you try.
```

### Task II: *Non-spatial manipulations*

For this one we will combine some of the ideas we learnt in the [previous block](../bB/lab_B) with this one.

Focus on the LSOA `liv` layer and use it to do the following:

1. Calculate the area of each neighbourhood
1. Find the five smallest areas in the table. Create a new object (e.g. `smallest` with them only)
1. Create a multi-layer map of Liverpool where the five smallest areas are coloured in red, and the rest appear in black.

### Task III: *The gender gap on the streets*

This one is a bit more advanced, so don't despair if you can't get it on your first try. It also relies on the {ref}`streets dataset from the "Hands-on" section <lab_C:streets>`, so you will need to load it up on your own. Here're the questions for you to answer:

> *Which group accounts for longer total street length in Zaragoza: men or women? By how much*?

The suggestion is that you get to work right away. However, if this task seems too daunting, you can expand the tip below for a bit of help.

```{tip}
:class: dropdown

Answering those two questions involves the following steps:
1. You will need your spatial data projected, so they are expressed in metres, and the length calculation makes sense. Check out the {ref}`section on transforming the CRS <lab_C:to_crs>`, and use, for example `EPSG:25830` as the target CRS.
1. Separate streets named after men from those named after women, perhaps in two objects (`men`, `women`) that contain the streets for each group. This is a non-spatial query at its heart, so make sure to revisit {ref}`that section on the previous block <lab_B:condition_queries>`.
1. Calculate the length of each street in each group. Refresh your memory of this in {ref}`this section <lab_C:length>`.
1. Create a total length by group by adding the lengths of each street. This is again a non-spatial operation (sum), so make sure to re-read {ref}`this part <lab_B:new_columns>` of Block B.
1. Compare the two and answer the questions. 

Surprised by the solution? Perhaps not, but remember data analysis is not only about discovering the unexpected, but about providing evidence of the things we *"know"* so we can build better arguments about actions.
```